# Requirements to collpase requirements tables Note + Making Concordances Concord - Tony Gui

In [1]:
import pandas as pd
import numpy as np
from dotenv import dotenv_values, find_dotenv
import os
import re
from data_cleaning_functions import requirements_clean, concordance_PCE_clean, \
    find_intermediate_industries, concordance_PCQ_clean, get_sales_from_make_matrix, clean_make_matrix, pce_tables_clean
from pathlib import Path
import warnings
warnings.filterwarnings('ignore', category=FutureWarning, message=".*concatenation with empty or all-NA entries is deprecated.*")

script_dir = str(Path().resolve().parent)
file_path = os.path.join(script_dir) + "/" 
Shapiro_data =  file_path + "Shapiro_data"
raw_data_path = file_path + "raw_bea_data" 

/opt/homebrew/lib/python3.11/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm, trange


In [49]:
BEA_expenditure = pd.read_excel(r"B:\OneDrive - DAZ\Desktop\Shapiro-by-Tony\raw_bea_data\BEA Monthly Expenditures.xlsx")
BEA_Price = pd.read_excel(r"B:\OneDrive - DAZ\Desktop\Shapiro-by-Tony\raw_bea_data\BEA Monthly Prices.xlsx")
BEA_Quantity = pd.read_excel(r"B:\OneDrive - DAZ\Desktop\Shapiro-by-Tony\raw_bea_data\BEA Monthly Quantity Data.xlsx")

In [3]:
BEA_expenditure = pd.read_excel(r'/Users/tonygui/Documents/Bank of Canada/shocks_productionnetworks/raw_bea_data/BEA Monthly Expenditures.xlsx')
BEA_expenditure

Table 2.4.5U. Personal Consumption Expenditures by Type of Product  \
0    [Millions of dollars; quarters and months are ...                   
1                          Bureau of Economic Analysis                   
2    Last Revised on: October 31, 2024 - Next Relea...                   
3                                                  NaN                   
4                                                 Line                   
..                                                 ...                   
415                                Legend / Footnotes:                   
416                    n.e.c. Not elsewhere classified                   
417  1. Consists of gasoline and other energy goods...                   
418  2. Food consists of food and beverages purchas...                   
419  Note.The figures in parentheses are the line n...                   

    Unnamed: 1 Unnamed: 2 Unnamed: 3 Unnamed: 4 Unnamed: 5 Unnamed: 6  \
0          NaN        NaN        NaN        NaN        NaN        NaN   
1          NaN        NaN        NaN        NaN        NaN        NaN   
2          NaN        NaN        NaN        NaN        NaN        NaN   
3          NaN        NaN        NaN        NaN        NaN        NaN   
4          NaN       1959        NaN        NaN        NaN        NaN   
..         ...        ...        ...        ...        ...        ...   
415        NaN        NaN        NaN        NaN        NaN        NaN   
416        NaN        NaN        NaN        NaN        NaN        NaN   
417        NaN        NaN        NaN        NaN        NaN        NaN   
418        NaN        NaN        NaN        NaN        NaN        NaN   
419        NaN        NaN        NaN        NaN        NaN        NaN   

    Unnamed: 7 Unnamed: 8 Unnamed: 9  ... Unnamed: 781 Unnamed: 782  \
0          NaN        NaN        NaN  ...          NaN          NaN   
1          NaN        NaN        NaN  ...          NaN          NaN   
2          NaN        NaN        NaN  ...          NaN          NaN   
3          NaN        NaN        NaN  ...          NaN          NaN   
4          NaN        NaN        NaN  ...          NaN         2024   
..         ...        ...        ...  ...          ...          ...   
415        NaN        NaN        NaN  ...          NaN          NaN   
416        NaN        NaN        NaN  ...          NaN          NaN   
417        NaN        NaN        NaN  ...          NaN          NaN   
418        NaN        NaN        NaN  ...          NaN          NaN   
419        NaN        NaN        NaN  ...          NaN          NaN   

    Unnamed: 783 Unnamed: 784 Unnamed: 785 Unnamed: 786 Unnamed: 787  \
0            NaN          NaN          NaN          NaN          NaN   
1            NaN          NaN          NaN          NaN          NaN   
2            NaN          NaN          NaN          NaN          NaN   
3            NaN          NaN          NaN          NaN          NaN   
4            NaN          NaN          NaN          NaN          NaN   
..           ...          ...          ...          ...          ...   
415          NaN          NaN          NaN          NaN          NaN   
416          NaN          NaN          NaN          NaN          NaN   
417          NaN          NaN          NaN          NaN          NaN   
418          NaN          NaN          NaN          NaN          NaN   
419          NaN          NaN          NaN          NaN          NaN   

    Unnamed: 788 Unnamed: 789 Unnamed: 790  
0            NaN          NaN          NaN  
1            NaN          NaN          NaN  
2            NaN          NaN          NaN  
3            NaN          NaN          NaN  
4            NaN          NaN          NaN  
..           ...          ...          ...  
415          NaN          NaN          NaN  
416          NaN          NaN          NaN  
417          NaN          NaN          NaN  
418          NaN          NaN          NaN  
419          NaN         

In [5]:
def clean_bea(df):
    df = df.iloc[6:, 1:]
    df["Unnamed: 1"] = df["Unnamed: 1"].str.lower()
    df["Unnamed: 1"] = df["Unnamed: 1"].str.strip()
    df = df.set_index(df.columns[0])
    start_date = '1959-01'
    num_columns = df.shape[1]
    new_columns = pd.date_range(start=start_date, periods=num_columns, freq='MS')
    df.columns = new_columns
    df.index.name = 'PCE Category'
    return df

In [6]:
BEA_expenditure = clean_bea(BEA_expenditure)

In [7]:
BEA_expenditure

1959-01-01 1959-02-01 1959-03-01 1959-04-01  \
PCE Category                                                                    
personal consumption expenditures     306091     309554     312702     312193   
goods                                 167411     169596     172162     170680   
durable goods                          42295      44207      44445      45065   
motor vehicles and parts               16904      18467      18900      19436   
new motor vehicles (55)                12525      13454      14068      14166   
...                                      ...        ...        ...        ...   
NaN                                      NaN        NaN        NaN        NaN   
NaN                                      NaN        NaN        NaN        NaN   
NaN                                      NaN        NaN        NaN        NaN   
NaN                                      NaN        NaN        NaN        NaN   
NaN                                      NaN        NaN        NaN        NaN   

                                  1959-05-01 1959-06-01 1959-07-01 1959-08-01  \
PCE Category                                                                    
personal consumption expenditures     316130     318193     317787     320161   
goods                                 173326     173845     172707     174065   
durable goods                          45359      45971      45408      46189   
motor vehicles and parts               19315      19254      19349      19906   
new motor vehicles (55)                14065      14000      14532      15131   
...                                      ...        ...        ...        ...   
NaN                                      NaN        NaN        NaN        NaN   
NaN                                      NaN        NaN        NaN        NaN   
NaN                                      NaN        NaN        NaN        NaN   
NaN                                      NaN        NaN        NaN        NaN   
NaN                                      NaN        NaN        NaN        NaN   

                                  1959-09-01 1959-10-01  ... 2023-12-01  \
PCE Category                                             ...              
personal consumption expenditures     324228     322794  ...   19289914   
goods                                 176799     174543  ...    6202719   
durable goods                          47410      44791  ...    2156473   
motor vehicles and parts               20963      18211  ...     737056   
new motor vehicles (55)                15221      13680  ...     398158   
...                                      ...        ...  ...        ...   
NaN                                      NaN        NaN  ...        NaN   
NaN                                      NaN        NaN  ...        NaN   
NaN                                      NaN        NaN  ...        NaN   
NaN                                      NaN        NaN  ...        NaN   
NaN                                      NaN        NaN  ...        NaN   

                                  2024-01-01 2024-02-01 2024-03-01 2024-04-01  \
PCE Category                                                                    
personal consumption expenditures   19308453   19412699   19553172   19603274   
goods                                6115814    6134233    6196511    6185979   
durable goods                        2112980    2128647    2140322    2129314   
motor vehicles and parts              704032     717274     714321     717296   
new motor vehicles (55)               372477     385054     385210     392087   
...                                      ...        ...        ...        ...   
NaN                                      NaN        NaN        NaN        NaN   
NaN                                      NaN        NaN        NaN        NaN   
NaN                                      NaN        NaN        NaN        NaN   
NaN                                      NaN        NaN    

In [8]:
shaprio_products = pd.read_excel(r'/Users/tonygui/Documents/Bank of Canada/shocks_productionnetworks/Shapiro/shaprio_products.xlsx')
shaprio_products["Products"] = shaprio_products["Products"].str.lower()
shaprio_products["Products"] = shaprio_products["Products"].str.strip()

shaprio_products

Unnamed: 0                                           Products
0             0                                          new autos
1             1                                   new light trucks
2             2                                         used autos
3             3                                  used light trucks
4             4                                              tires
..          ...                                                ...
125         125                     repair of household appliances
126         126                           other household services
127         127             foreign travel by u.s. residents (129)
128         128  less: expenditures in the united states by non...
129         129  final consumption expenditures of nonprofit in...

[130 rows x 2 columns]

In [10]:
BEA_expenditure["Shaprio?"] = BEA_expenditure.index.isin(shaprio_products["Products"]).astype(int)

/var/folders/bs/21p_36y97dqfc1wddk8jv1vw0000gn/T/ipykernel_8692/3739665217.py:1: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  BEA_expenditure["Shaprio?"] = BEA_expenditure.index.isin(shaprio_products["Products"]).astype(int)


In [12]:
BEA_expenditure
BEA_expenditure = BEA_expenditure[[BEA_expenditure.columns[-1]] + BEA_expenditure.columns[:-1].tolist()]

BEA_expenditure.to_excel("dummy.xlsx")

In [51]:
BEA_Quantity = clean_bea(BEA_Quantity)

In [13]:
BEA_Quantity

NameError: name 'BEA_Quantity' is not defined

In [58]:
merged_df = BEA_Quantity.merge(shaprio_products, left_index=True, right_on="Products", how='inner')
merged_df.set_index("Products", inplace=True)
merged_df

1959-01-01 00:00:00  \
Products                                                                 
new autos                                                       46.147   
new light trucks                                                 0.596   
used autos                                                      28.445   
used light trucks                                                0.274   
tires                                                            9.206   
...                                                                ...   
foreign travel by u.s. residents (129)                           8.851   
less: expenditures in the united states by nonr...               4.953   
final consumption expenditures of nonprofit ins...               2.467   
religious organizations' services to households                 37.864   
foundations and grantmaking and giving services...               1.768   

                                                   1959-02-01 00:00:00  \
Products                                                                 
new autos                                                       49.551   
new light trucks                                                 0.648   
used autos                                                      36.379   
used light trucks                                                0.295   
tires                                                            9.354   
...                                                                ...   
foreign travel by u.s. residents (129)                           8.827   
less: expenditures in the united states by nonr...                4.78   
final consumption expenditures of nonprofit ins...               2.498   
religious organizations' services to households                 39.156   
foundations and grantmaking and giving services...               1.808   

                                                   1959-03-01 00:00:00  \
Products                                                                 
new autos                                                       51.565   
new light trucks                                                 0.693   
used autos                                                      34.029   
used light trucks                                                0.313   
tires                                                            9.318   
...                                                                ...   
foreign travel by u.s. residents (129)                           8.777   
less: expenditures in the united states by nonr...               4.606   
final consumption expenditures of nonprofit ins...               2.499   
religious organizations' services to households                 40.359   
foundations and grantmaking and giving services...               1.899   

                                                   1959-04-01 00:00:00  \
Products                                                                 
new autos                                                        52.01   
new light trucks                                                 0.706   
used autos                                                      39.255   
used light trucks                                                0.316   
tires                                                            9.412   
...                                                                ...   
foreign travel by u.s. residents (129)                           8.707   
less: expenditures in the united states by nonr...               4.392   
final consumption expenditures of nonprofit ins...               2.474   
religious organizations' services to households                 41.533   
foundations and grantmaking and giving services...               1.958   

                                                   1959-05-01 00:00:00  \
Products                                                                 
new autos                                          

In [60]:
# Find duplicated index
dup_index = merged_df.index[merged_df.index.duplicated()].unique()

# Drop the first occurrence for each duplicated index value
for idx in dup_index:
    merged_df.drop(index=idx, inplace=True)
    break  # Remove only one row with a repeated index

merged_df

1959-01-01 00:00:00  \
Products                                                                 
new autos                                                       46.147   
new light trucks                                                 0.596   
used autos                                                      28.445   
used light trucks                                                0.274   
tires                                                            9.206   
...                                                                ...   
other household services                                         2.648   
foreign travel by u.s. residents (129)                           8.851   
less: expenditures in the united states by nonr...               4.953   
final consumption expenditures of nonprofit ins...               2.467   
foundations and grantmaking and giving services...               1.768   

                                                   1959-02-01 00:00:00  \
Products                                                                 
new autos                                                       49.551   
new light trucks                                                 0.648   
used autos                                                      36.379   
used light trucks                                                0.295   
tires                                                            9.354   
...                                                                ...   
other household services                                         2.737   
foreign travel by u.s. residents (129)                           8.827   
less: expenditures in the united states by nonr...                4.78   
final consumption expenditures of nonprofit ins...               2.498   
foundations and grantmaking and giving services...               1.808   

                                                   1959-03-01 00:00:00  \
Products                                                                 
new autos                                                       51.565   
new light trucks                                                 0.693   
used autos                                                      34.029   
used light trucks                                                0.313   
tires                                                            9.318   
...                                                                ...   
other household services                                         2.825   
foreign travel by u.s. residents (129)                           8.777   
less: expenditures in the united states by nonr...               4.606   
final consumption expenditures of nonprofit ins...               2.499   
foundations and grantmaking and giving services...               1.899   

                                                   1959-04-01 00:00:00  \
Products                                                                 
new autos                                                        52.01   
new light trucks                                                 0.706   
used autos                                                      39.255   
used light trucks                                                0.316   
tires                                                            9.412   
...                                                                ...   
other household services                                         2.828   
foreign travel by u.s. residents (129)                           8.707   
less: expenditures in the united states by nonr...               4.392   
final consumption expenditures of nonprofit ins...               2.474   
foundations and grantmaking and giving services...               1.958   

                                                   1959-05-01 00:00:00  \
Products                                                                 
new autos                                          

# 1. Load in Requirements Matrix 

In [45]:
requirements = pd.read_excel(os.path.join(raw_data_path, 'IxI_TR_2017_PRO_Det.xlsx'), sheet_name='2017')
requirements = requirements_clean(requirements, wide=True)
requirements

desc_O                                             abrasive product manufacturing  \
desc_I                                                                              
abrasive product manufacturing                                           1.050968   
accommodation                                                            0.001625   
accounting, tax preparation, bookkeeping, and p...                       0.004291   
adhesive manufacturing                                                   0.009834   
advertising, public relations, and related serv...                       0.003618   
...                                                                           ...   
wineries                                                                 0.000031   
wired telecommunications carriers                                         0.00784   
wireless telecommunications carriers (except sa...                       0.002042   
wiring device manufacturing                                              0.000123   
wood kitchen cabinet and countertop manufacturing                         0.00007   

desc_O                                             accommodation  \
desc_I                                                             
abrasive product manufacturing                          0.000104   
accommodation                                           1.002916   
accounting, tax preparation, bookkeeping, and p...      0.006341   
adhesive manufacturing                                  0.000675   
advertising, public relations, and related serv...      0.011064   
...                                                          ...   
wineries                                                0.002531   
wired telecommunications carriers                       0.005068   
wireless telecommunications carriers (except sa...       0.00384   
wiring device manufacturing                             0.000333   
wood kitchen cabinet and countertop manufacturing        0.00017   

desc_O                                             accounting, tax preparation, bookkeeping, and payroll services  \
desc_I                                                                                                              
abrasive product manufacturing                                                               0.000036               
accommodation                                                                                0.008541               
accounting, tax preparation, bookkeeping, and p...                                           1.029665               
adhesive manufacturing                                                                       0.000125               
advertising, public relations, and related serv...                                            0.00433               
...                                                                                               ...               
wineries                                                                                     0.000194               
wired telecommunications carriers                                                            0.003881               
wireless telecommunications carriers (except sa...                                           0.003834               
wiring device manufacturing                                                                  0.000089               
wood kitchen cabinet and countertop manufacturing                                            0.000055               

desc_O                                             adhesive manufacturing  \
desc_I                                                                      
abrasive product manufacturing                                   0.000313   
accommodation                                                    0.002069   
accounting, tax preparation, bookkeeping, and p...               0.004638   
adhesive manufacturing                                            1.01569   
advertising, public relat

# 2. Calculate Delta

In [46]:
requirements = requirements.T
with pd.option_context("future.no_silent_downcasting", True):
    requirements = requirements.fillna(0).infer_objects(copy=False)
delta = np.identity(len(requirements)) - np.linalg.inv(requirements)

# 2 (Making Concordances Concord) Adding Scrap, Used and secondhand goods and ROW adjustments to Delta

In [47]:
"""These 4 industries are found in the concordance table but not in the Reqirements table so I am 
adding them manually with row and column inputs of zero"""
concordance_but_not_requirments = ["Scrap", "Used and secondhand goods", "Rest of the world adjustment", "noncomparable imports"] 
delta = pd.DataFrame(delta, index=requirements.index, columns=requirements.columns)
delta = delta.reindex(index=requirements.index.append(pd.Index(concordance_but_not_requirments)).str.lower() , columns=requirements.columns.append(pd.Index(concordance_but_not_requirments)).str.lower() , fill_value=0)
delta

abrasive product manufacturing  \
abrasive product manufacturing                                        4.838435e-02   
accommodation                                                         9.403910e-07   
accounting, tax preparation, bookkeeping, and p...                    6.624357e-09   
adhesive manufacturing                                                1.512516e-07   
advertising, public relations, and related serv...                    5.000129e-05   
...                                                                            ...   
wood kitchen cabinet and countertop manufacturing                     5.349439e-04   
scrap                                                                 0.000000e+00   
used and secondhand goods                                             0.000000e+00   
rest of the world adjustment                                          0.000000e+00   
noncomparable imports                                                 0.000000e+00   

                                                    accommodation  \
abrasive product manufacturing                           0.000443   
accommodation                                            0.000878   
accounting, tax preparation, bookkeeping, and p...       0.006421   
adhesive manufacturing                                   0.000273   
advertising, public relations, and related serv...       0.002832   
...                                                           ...   
wood kitchen cabinet and countertop manufacturing        0.002026   
scrap                                                    0.000000   
used and secondhand goods                                0.000000   
rest of the world adjustment                             0.000000   
noncomparable imports                                    0.000000   

                                                    accounting, tax preparation, bookkeeping, and payroll services  \
abrasive product manufacturing                                                               0.001414                
accommodation                                                                                0.003049                
accounting, tax preparation, bookkeeping, and p...                                           0.026392                
adhesive manufacturing                                                                       0.000493                
advertising, public relations, and related serv...                                           0.001890                
...                                                                                               ...                
wood kitchen cabinet and countertop manufacturing                                            0.004485                
scrap                                                                                        0.000000                
used and secondhand goods                                                                    0.000000                
rest of the world adjustment                                                                 0.000000                
noncomparable imports                                                                        0.000000                

                                                    adhesive manufacturing  \
abrasive product manufacturing                                8.256050e-03   
accommodation                                                 1.710807e-05   
accounting, tax preparation, bookkeeping, and p...            9.531542e-08   
adhesive manufacturing                                        1.424958e-02   
advertising, public relations, and related serv...            2.589963e-05   
...                                                                    ...   
wood kitchen cabinet and countertop manufacturing             4.085440e-03   
scrap                                                         0.000000e+00   
used and secondhand goods                                     0.000000e

# 2.5b Making Negative Values in Delta Zero

In [48]:
negative_count = (delta < 0).sum().sum()
x = negative_count/402**2
delta[delta < 0] = 0
negative_count_new = (delta < 0).sum().sum()
y = negative_count_new/402**2

# 2.5b Force negatives to be zero but adjust row sums to be same as before

In [49]:
# V = delta.sum(axis=0)
# P = delta[delta > 0].sum()
# delta.loc['norm'] = V/P
# last_values = delta.iloc[-1]
# delta[delta < 0] = 0
# delta = delta.iloc[:-1].div(last_values)
# delta

# Dealting with Intermediate Industries - Making Concordances Concord Section 3.3.1. - Operationalizing Industries without Products

# Step 1. Making Concordances Concord

In [50]:
use_table = pd.read_excel(os.path.join(raw_data_path, "Use_SUT_Framework_2017_DET.xlsx"), sheet_name="2017")
# peq_concordance = pd.read_excel(os.path.join(raw_data_path, "PEQBridge_2017_DET.xlsx"), sheet_name="2017")

# Returns all industries with zero PCE 
intermediate_industries = find_intermediate_industries(use_table)

# peq_concordance = concordance_PCQ_clean(peq_concordance)
# intermediate_industries = intermediate_industries[~intermediate_industries['Industry'].isin(peq_concordance['Industries'])]

intermediate_industries = intermediate_industries.iloc[:, [0]]
intermediate_industries = intermediate_industries.sort_values(by="Industry")
intermediate_industries

Industry
106               air and gas compressor manufacturing
163     aircraft engine and engine parts manufacturing
67          all other forging, stamping, and sintering
344  all other miscellaneous professional, scientif...
291                                   all other retail
..                                                 ...
81              valve and fittings other than plumbing
42   veneer, plywood, and engineered wood product m...
281  wholesale electronic markets and agents and br...
145                        wiring device manufacturing
173  wood kitchen cabinet and countertop manufacturing

[143 rows x 1 columns]

# Steps 2 - 5. Making Concordances Concord - Loop over Intermediate Industries and Remove

In [51]:
# requirements = pd.read_excel(os.path.join(raw_data_path, 'IxI_TR_2017_PRO_Det.xlsx'), sheet_name='2017')
# requirements = requirements_clean(requirements, wide=True)

make_matrix = pd.read_excel(os.path.join(raw_data_path, "Supply_2017_DET.xlsx"), sheet_name="2017")
make_matrix = clean_make_matrix(make_matrix)

# For the Loop 
big_lambda = np.eye(len(delta)) # create a big_lambda identity matrix that will become out final output
big_lambda = pd.DataFrame(big_lambda)
big_lambda = big_lambda.set_index(delta.index)
big_lambda.columns = delta.index
delta_industries = delta.index # save all the requirment table industries outside the loop 
removed = [] # stores all removed industries through the loop 

i = 0

for row in intermediate_industries.iloc[::-1].itertuples(): # looping backwards
    
    i += 1 
    current = row.Industry # industry we are currently removing
    # Create identity matrix for current loop iteration
    phi_i = np.eye(len(delta) - (i - 1))
    phi_i = pd.DataFrame(phi_i)
    phi_i = phi_i.set_index(delta_industries)
    phi_i.columns = delta_industries

    current_make_table = make_matrix.copy() # use a new make_matrix each time we do this
    current_make_table = current_make_table.loc[[current]] # the row of the make table associated with the current industry  
    current_make_table.drop(columns=[current], inplace=True) # drop the column associated with the current industry so we dont include it in our sum
    current_industry_sum = current_make_table.loc[current].sum() # find sum of row

    # just making sure that we aren't dividing by zero 
    if current_industry_sum != 0:
        current_make_table = current_make_table.astype(float)
        current_make_table.loc[current] = current_make_table.loc[current] / current_industry_sum


    current_make_table = current_make_table[sorted(current_make_table.columns)] # sort the normazlied row alphabetically

    # remove the current industry from intermediate list
    intermediate_industries = intermediate_industries[intermediate_industries['Industry'] != current]
    # drop the current industry column from phi_i and industry indexing
    phi_i = phi_i.drop(columns=current)
    delta_industries = delta_industries.drop(current) 
    # Remove all the industries we've previously removed in earlier loop iterations 
    current_make_table.drop(columns=removed, inplace=True)
    removed.append(current)

    # Update phi_i with the current industry sale shares
    phi_i.loc[current_make_table.index] = current_make_table.loc[current_make_table.index].astype(np.float64).values

    big_lambda = big_lambda @ phi_i

# Step 6. Making Concordances Concord - Converting IO matrix from sales shares to dollars

In [52]:
make_matrix = pd.read_excel(os.path.join(raw_data_path, "Supply_2017_DET.xlsx"), sheet_name="2017")
sales_vector = get_sales_from_make_matrix(make_matrix) # returns the sales for each industry

# these industries are not in the make matrix so i will add them manually with zero entries to preserve df sizes
industries_not_in_make_matrix = ["state and local government passenger transit", "state and local government electric utilities", \
                      "secondary smelting and alloying of aluminum", "federal electric utilities"]
not_in_make_matrix = pd.DataFrame({'Industries': industries_not_in_make_matrix, 'Sales': [0,0,0,0]})
sales_vector = pd.concat([sales_vector, not_in_make_matrix], ignore_index=True)
sales_vector.set_index('Industries', inplace=True)

# repeat the sales vector n times to make a sales matrix
sales_repeated = pd.DataFrame({f'{i}': sales_vector['Sales'].values for i in range(1, len(delta))})
sales_repeated.set_index(sales_vector.index, inplace=True)
sales_matrix = pd.concat([sales_vector, sales_repeated], axis=1)
sales_matrix.columns = delta.columns

# Y is IO matrix in dollars 
Y = delta * sales_matrix 
Y

abrasive product manufacturing  \
abrasive product manufacturing                                          228.567689   
accommodation                                                             0.205593   
accounting, tax preparation, bookkeeping, and p...                        0.001181   
adhesive manufacturing                                                    0.002301   
advertising, public relations, and related serv...                       20.129619   
...                                                                            ...   
wineries                                                                  0.000935   
wired telecommunications carriers                                         2.228930   
wireless telecommunications carriers (except sa...                       11.888784   
wiring device manufacturing                                              47.964272   
wood kitchen cabinet and countertop manufacturing                         7.704796   

                                                    accommodation  \
abrasive product manufacturing                           2.094217   
accommodation                                          192.013915   
accounting, tax preparation, bookkeeping, and p...    1144.328172   
adhesive manufacturing                                   4.148207   
advertising, public relations, and related serv...    1140.130796   
...                                                           ...   
wineries                                                 8.850143   
wired telecommunications carriers                      154.469546   
wireless telecommunications carriers (except sa...     435.642301   
wiring device manufacturing                              2.604689   
wood kitchen cabinet and countertop manufacturing       29.185953   

                                                    accounting, tax preparation, bookkeeping, and payroll services  \
abrasive product manufacturing                                                               6.682003                
accommodation                                                                              666.483337                
accounting, tax preparation, bookkeeping, and p...                                        4703.468696                
adhesive manufacturing                                                                       7.505241                
advertising, public relations, and related serv...                                         761.055401                
...                                                                                               ...                
wineries                                                                                    46.715622                
wired telecommunications carriers                                                         1213.142206                
wireless telecommunications carriers (except sa...                                        2167.581455                
wiring device manufacturing                                                                  5.969809                
wood kitchen cabinet and countertop manufacturing                                           64.595098                

                                                    adhesive manufacturing  \
abrasive product manufacturing                                   39.001581   
accommodation                                                     3.740252   
accounting, tax preparation, bookkeeping, and p...                0.016987   
adhesive manufacturing                                          216.778841   
advertising, public relations, and related serv...               10.426725   
...                                                                    ...   
wineries                                                          0.006415   
wired telecommunications carriers                                 0.247249   
wireless telecommunications carriers (except sa...                1.553

# Step 7. Making Concordances Concord - Value Added for the Economy

In [53]:
sum_Y = Y.sum(axis=1).to_frame()
sum_Y.columns = ['Sales']
VA_pre_transformation = (sales_vector - sum_Y).sum()

VA_pre_transformation

Sales    1.946673e+07
dtype: float64

# Step 8. Making Concordances Concord - IO Matrix in USD

In [54]:
# new IO matrix in USD 
Y_tilde = big_lambda.T @ Y @ big_lambda
sales_tilde = big_lambda.T @ sales_vector

# Verifing that economy wide value added is identical to the pre-transformation level
sum_Y_tilde = Y_tilde.sum(axis=1).to_frame()
sum_Y_tilde.columns = ['Sales']
VA_post_transformation = (sales_tilde - sum_Y_tilde).sum()
VA_post_transformation

Sales    1.736196e+07
dtype: float64

In [55]:
"""Pre transformation and post transformation are not the same"""

differnece = VA_post_transformation - VA_pre_transformation
differnece

Sales   -2.104772e+06
dtype: float64

# Step 9. Making Concordances Concord - Calculating New Delta

In [14]:
recip_sales = 1/sales_tilde
sales_tilde_repeated = pd.DataFrame({f'{i}': recip_sales['Sales'].values for i in range(1, len(delta))})
sales_tilde_repeated.set_index(recip_sales.index, inplace=True)
sales_tilde_matrix = pd.concat([recip_sales, sales_tilde_repeated], axis=1)
sales_tilde_matrix.columns = delta.columns

delta_tilde = Y_tilde * sales_tilde_matrix
delta = delta_tilde
delta

abrasive product manufacturing  \
abrasive product manufacturing                                            0.029256   
accommodation                                                             0.000137   
accounting, tax preparation, bookkeeping, and p...                        0.000005   
adhesive manufacturing                                                    0.000190   
advertising, public relations, and related serv...                        0.000052   
...                                                                            ...   
wood kitchen cabinet and countertop manufacturing                         0.000608   
scrap                                                                     0.000080   
used and secondhand goods                                                 0.000092   
rest of the world adjustment                                              0.000031   
noncomparable imports                                                     0.001764   

                                                    accommodation  \
abrasive product manufacturing                           0.001035   
accommodation                                            0.000852   
accounting, tax preparation, bookkeeping, and p...       0.006041   
adhesive manufacturing                                   0.000401   
advertising, public relations, and related serv...       0.002862   
...                                                           ...   
wood kitchen cabinet and countertop manufacturing        0.001696   
scrap                                                    0.000532   
used and secondhand goods                                0.000233   
rest of the world adjustment                             0.003069   
noncomparable imports                                    0.000867   

                                                    accounting, tax preparation, bookkeeping, and payroll services  \
abrasive product manufacturing                                                               0.005711                
accommodation                                                                                0.005845                
accounting, tax preparation, bookkeeping, and p...                                           0.023915                
adhesive manufacturing                                                                       0.001876                
advertising, public relations, and related serv...                                           0.003357                
...                                                                                               ...                
wood kitchen cabinet and countertop manufacturing                                            0.007081                
scrap                                                                                        0.002113                
used and secondhand goods                                                                    0.004554                
rest of the world adjustment                                                                 0.015160                
noncomparable imports                                                                        0.004243                

                                                    adhesive manufacturing  \
abrasive product manufacturing                                    0.005045   
accommodation                                                     0.000126   
accounting, tax preparation, bookkeeping, and p...                0.000007   
adhesive manufacturing                                            0.012172   
advertising, public relations, and related serv...                0.000038   
...                                                                    ...   
wood kitchen cabinet and countertop manufacturing                 0.002907   
scrap                                                             0.000180   
used and secondhand goods                                         0.000

# End of Making Concordances Concord - Back to Requirements to Collapse Requirements Table

# 3. Merge Concordance with Delta

In [15]:
concordance = pd.read_excel(os.path.join(raw_data_path, "PCEBridge_2017_DET.xlsx"), sheet_name="2017")
concordance = concordance_PCE_clean(concordance)
concordance

PCE Bridge Products  \
4                                   new domestic autos   
5                                   new domestic autos   
6                                    new foreign autos   
7                                     new light trucks   
8                                           used autos   
..                                                 ...   
702  final consumption expenditures of nonprofit in...   
703  final consumption expenditures of nonprofit in...   
704  final consumption expenditures of nonprofit in...   
705  final consumption expenditures of nonprofit in...   
706  final consumption expenditures of nonprofit in...   

                                 PCE Bridge Industries  
4                             automobile manufacturing  
5                     motor vehicle body manufacturing  
6                             automobile manufacturing  
7        light truck and utility vehicle manufacturing  
8                                                scrap  
..                                                 ...  
702         museums, historical sites, zoos, and parks  
703          other amusement and recreation industries  
704                            religious organizations  
705  grantmaking, giving, and social advocacy organ...  
706  civic, social, professional, and similar organ...  

[703 rows x 2 columns]

In [16]:
"""the problem here is some industries in the requirments matrix still have no match to PCE they are matching to PEQ so i must drop them here when im trying to 
make the requirments table in terms of products however im not sure if this changes some of the math performed to the requirments matrix ie delta later on
"""
industries_in_requirments = set(delta.columns)
indsutries_in_concordance = set(concordance["PCE Bridge Industries"])
industires_not_in_concordance = industries_in_requirments - indsutries_in_concordance
delta = delta.drop(index=industires_not_in_concordance, columns=industires_not_in_concordance, errors='ignore')
delta

abrasive product manufacturing  \
abrasive product manufacturing                                            0.029256   
accommodation                                                             0.000137   
accounting, tax preparation, bookkeeping, and p...                        0.000005   
adhesive manufacturing                                                    0.000190   
advertising, public relations, and related serv...                        0.000052   
...                                                                            ...   
wireless telecommunications carriers (except sa...                        0.000086   
scrap                                                                     0.000080   
used and secondhand goods                                                 0.000092   
rest of the world adjustment                                              0.000031   
noncomparable imports                                                     0.001764   

                                                    accommodation  \
abrasive product manufacturing                           0.001035   
accommodation                                            0.000852   
accounting, tax preparation, bookkeeping, and p...       0.006041   
adhesive manufacturing                                   0.000401   
advertising, public relations, and related serv...       0.002862   
...                                                           ...   
wireless telecommunications carriers (except sa...       0.001987   
scrap                                                    0.000532   
used and secondhand goods                                0.000233   
rest of the world adjustment                             0.003069   
noncomparable imports                                    0.000867   

                                                    accounting, tax preparation, bookkeeping, and payroll services  \
abrasive product manufacturing                                                               0.005711                
accommodation                                                                                0.005845                
accounting, tax preparation, bookkeeping, and p...                                           0.023915                
adhesive manufacturing                                                                       0.001876                
advertising, public relations, and related serv...                                           0.003357                
...                                                                                               ...                
wireless telecommunications carriers (except sa...                                           0.011313                
scrap                                                                                        0.002113                
used and secondhand goods                                                                    0.004554                
rest of the world adjustment                                                                 0.015160                
noncomparable imports                                                                        0.004243                

                                                    adhesive manufacturing  \
abrasive product manufacturing                                    0.005045   
accommodation                                                     0.000126   
accounting, tax preparation, bookkeeping, and p...                0.000007   
adhesive manufacturing                                            0.012172   
advertising, public relations, and related serv...                0.000038   
...                                                                    ...   
wireless telecommunications carriers (except sa...                0.000138   
scrap                                                             0.000180   
used and secondhand goods                                         0.000

In [ ]:
in_num_products = concordance['PCE Bridge Industries'].value_counts()

delta_product_columns = pd.DataFrame(index=delta.index, columns=concordance['PCE Bridge Products'])

for column in delta_product_columns: 
    industry = concordance.loc[concordance['PCE Bridge Products'] == column, 'PCE Bridge Industries'].values
    delta_product_columns[column] = delta[industry] / in_num_products[industry]

delta_product_cr = pd.DataFrame(columns=delta_product_columns.columns)
lst_for_industry = []
for row in delta_product_columns.index:
    final_value = delta_product_columns.loc[row] / in_num_products[row]
    products = concordance[concordance['PCE Bridge Industries'] == row]['PCE Bridge Products'].tolist()
    for product in products: 
        lst_for_industry.append(row)
        final_value_row = pd.DataFrame(final_value).T
        final_value_row.index = [product]
        
        delta_product_cr = pd.concat([delta_product_cr, final_value_row])

industry = pd.DataFrame(lst_for_industry, columns=['industry'])
industry.index = delta_product_cr.index
delta_product_cr = pd.concat([delta_product_cr, industry], axis = 1)
delta_product_cr

new domestic autos  \
tools, hardware, and supplies                             1.154050e-05   
group housing                                             6.950080e-07   
amusement parks, campgrounds, and related recre...        6.950080e-07   
hotels and motels                                         6.950080e-07   
housing at schools                                        6.950080e-07   
...                                                                ...   
less: expenditures in the united states by nonr...        3.088450e-06   
government employees' expenditures abroad                 8.582072e-06   
private employees' expenditures abroad                    8.582072e-06   
u.s. travel outside the united states                     8.582072e-06   
u.s. student expenditures                                 8.582072e-06   

                                                    new domestic autos  \
tools, hardware, and supplies                                 0.000020   
group housing                                                 0.000011   
amusement parks, campgrounds, and related recre...            0.000011   
hotels and motels                                             0.000011   
housing at schools                                            0.000011   
...                                                                ...   
less: expenditures in the united states by nonr...            0.000010   
government employees' expenditures abroad                     0.000024   
private employees' expenditures abroad                        0.000024   
u.s. travel outside the united states                         0.000024   
u.s. student expenditures                                     0.000024   

                                                    new foreign autos  \
tools, hardware, and supplies                            1.154050e-05   
group housing                                            6.950080e-07   
amusement parks, campgrounds, and related recre...       6.950080e-07   
hotels and motels                                        6.950080e-07   
housing at schools                                       6.950080e-07   
...                                                               ...   
less: expenditures in the united states by nonr...       3.088450e-06   
government employees' expenditures abroad                8.582072e-06   
private employees' expenditures abroad                   8.582072e-06   
u.s. travel outside the united states                    8.582072e-06   
u.s. student expenditures                                8.582072e-06   

                                                    new light trucks  \
tools, hardware, and supplies                           4.591691e-07   
group housing                                           4.294312e-08   
amusement parks, campgrounds, and related recre...      4.294312e-08   
hotels and motels                                       4.294312e-08   
housing at schools                                      4.294312e-08   
...                                                              ...   
less: expenditures in the united states by nonr...      2.294811e-07   
government employees' expenditures abroad               1.004892e-06   
private employees' expenditures abroad                  1.004892e-06   
u.s. travel outside the united states                   1.004892e-06   
u.s. student expenditures                               1.004892e-06   

                                                      used autos  \
tools, hardware, and supplies                       9.951325e-06   
group housing                                       5.090999e-07   
amusement parks, campgrounds, and related recre...  5.090999e-07   
hotels and motels                                   5.090999e-07   
housing at schools                                  5.090999e-07   
...                                                          ...   
less: expenditures in the united states by nonr...  1.97

# 4. Collapse columns

In [18]:
delta_products = delta_product_cr.T.groupby(delta_product_cr.columns).sum().T
delta_products

accessories and parts  \
tools, hardware, and supplies                                   0.007275   
group housing                                                   0.000399   
amusement parks, campgrounds, and related recre...              0.000399   
hotels and motels                                               0.000399   
housing at schools                                              0.000399   
...                                                                  ...   
less: expenditures in the united states by nonr...              0.001175   
government employees' expenditures abroad                       0.003612   
private employees' expenditures abroad                          0.003612   
u.s. travel outside the united states                           0.003612   
u.s. student expenditures                                       0.003612   

                                                   air transportation  \
tools, hardware, and supplies                                0.000458   
group housing                                                0.000019   
amusement parks, campgrounds, and related recre...           0.000019   
hotels and motels                                            0.000019   
housing at schools                                           0.000019   
...                                                               ...   
less: expenditures in the united states by nonr...           0.000352   
government employees' expenditures abroad                    0.000083   
private employees' expenditures abroad                       0.000083   
u.s. travel outside the united states                        0.000083   
u.s. student expenditures                                    0.000083   

                                                   alcohol in purchased meals  \
tools, hardware, and supplies                                        0.003963   
group housing                                                        0.001152   
amusement parks, campgrounds, and related recre...                   0.001152   
hotels and motels                                                    0.001152   
housing at schools                                                   0.001152   
...                                                                       ...   
less: expenditures in the united states by nonr...                   0.002213   
government employees' expenditures abroad                            0.000903   
private employees' expenditures abroad                               0.000903   
u.s. travel outside the united states                                0.000903   
u.s. student expenditures                                            0.000903   

                                                   all other professional medical services  \
tools, hardware, and supplies                                                     0.000174   
group housing                                                                      0.00002   
amusement parks, campgrounds, and related recre...                                 0.00002   
hotels and motels                                                                  0.00002   
housing at schools                                                                 0.00002   
...                                                                                    ...   
less: expenditures in the united states by nonr...                                0.000039   
government employees' expenditures abroad                                         0.002489   
private employees' expenditures abroad                                            0.002489   
u.s. travel outside the united states                                             0.002489   
u.s. student expenditures                                                         0.002489   

                                                   amusement parks, campgrounds, and related recreational services  \
tools, hardware, and supplies            

# 5. Make Matrix to Sales

In [19]:
make_matrix = pd.read_excel(os.path.join(raw_data_path, "Supply_2017_DET.xlsx"), sheet_name='2017')
sales = get_sales_from_make_matrix(make_matrix)
sales

3                                          Industries   Sales
0                                     oilseed farming   37922
1                                       grain farming   66790
2                         vegetable and melon farming   18582
3                          fruit and tree nut farming   29731
4    greenhouse, nursery, and floriculture production   19868
..                                                ...     ...
397      other state and local government enterprises  107059
398                                             scrap   10763
399                         used and secondhand goods       0
400                             noncomparable imports       0
401                      rest of the world adjustment    3468

[402 rows x 2 columns]

# 6. Merge concordance with sales 

In [20]:
product_sales = pd.merge(concordance, sales, left_on='PCE Bridge Industries', right_on='Industries')
product_sales = product_sales[["PCE Bridge Products", "Industries", 'Sales']]
product_sales

PCE Bridge Products  \
0                                   new domestic autos   
1                                   new domestic autos   
2                                    new foreign autos   
3                                     new light trucks   
4                                           used autos   
..                                                 ...   
698  final consumption expenditures of nonprofit in...   
699  final consumption expenditures of nonprofit in...   
700  final consumption expenditures of nonprofit in...   
701  final consumption expenditures of nonprofit in...   
702  final consumption expenditures of nonprofit in...   

                                            Industries   Sales  
0                             automobile manufacturing   32758  
1                     motor vehicle body manufacturing   10556  
2                             automobile manufacturing   32758  
3        light truck and utility vehicle manufacturing  215421  
4                                                scrap   10763  
..                                                 ...     ...  
698         museums, historical sites, zoos, and parks   20894  
699          other amusement and recreation industries   81734  
700                            religious organizations  100202  
701  grantmaking, giving, and social advocacy organ...   58458  
702  civic, social, professional, and similar organ...   95191  

[703 rows x 3 columns]

# 7. Group sum of Sales for every Product

In [21]:
# calculates the number of product categories an Industry belongs to 
product_sales['In#Products'] = product_sales['Industries'].map(product_sales['Industries'].value_counts())
product_sales["Ratio_in_Product"] = product_sales['Sales'] / product_sales['In#Products'] 
product_sales['Sales_Sum'] = product_sales.groupby('PCE Bridge Products')['Ratio_in_Product'].transform('sum')
product_sales

PCE Bridge Products  \
0                                   new domestic autos   
1                                   new domestic autos   
2                                    new foreign autos   
3                                     new light trucks   
4                                           used autos   
..                                                 ...   
698  final consumption expenditures of nonprofit in...   
699  final consumption expenditures of nonprofit in...   
700  final consumption expenditures of nonprofit in...   
701  final consumption expenditures of nonprofit in...   
702  final consumption expenditures of nonprofit in...   

                                            Industries   Sales  In#Products  \
0                             automobile manufacturing   32758            2   
1                     motor vehicle body manufacturing   10556            1   
2                             automobile manufacturing   32758            2   
3        light truck and utility vehicle manufacturing  215421            1   
4                                                scrap   10763            6   
..                                                 ...     ...          ...   
698         museums, historical sites, zoos, and parks   20894            3   
699          other amusement and recreation industries   81734            3   
700                            religious organizations  100202            2   
701  grantmaking, giving, and social advocacy organ...   58458            3   
702  civic, social, professional, and similar organ...   95191            4   

     Ratio_in_Product     Sales_Sum  
0        16379.000000  2.693500e+04  
1        10556.000000  2.693500e+04  
2        16379.000000  1.637900e+04  
3       215421.000000  2.154210e+05  
4         1793.833333  1.793833e+03  
..                ...           ...  
698       6964.666667  1.554667e+06  
699      27244.666667  1.554667e+06  
700      50101.000000  1.554667e+06  
701      19486.000000  1.554667e+06  
702      23797.750000  1.554667e+06  

[703 rows x 6 columns]

# 8. Sales Share 

In [22]:
product_sales['Sale Share'] = product_sales["Ratio_in_Product"] / product_sales["Sales_Sum"]
product_sales = product_sales.rename(columns={'Industries': 'industry'})
product_sales = product_sales.rename(columns={'PCE Bridge Products': 'product'})
product_sales

product  \
0                                   new domestic autos   
1                                   new domestic autos   
2                                    new foreign autos   
3                                     new light trucks   
4                                           used autos   
..                                                 ...   
698  final consumption expenditures of nonprofit in...   
699  final consumption expenditures of nonprofit in...   
700  final consumption expenditures of nonprofit in...   
701  final consumption expenditures of nonprofit in...   
702  final consumption expenditures of nonprofit in...   

                                              industry   Sales  In#Products  \
0                             automobile manufacturing   32758            2   
1                     motor vehicle body manufacturing   10556            1   
2                             automobile manufacturing   32758            2   
3        light truck and utility vehicle manufacturing  215421            1   
4                                                scrap   10763            6   
..                                                 ...     ...          ...   
698         museums, historical sites, zoos, and parks   20894            3   
699          other amusement and recreation industries   81734            3   
700                            religious organizations  100202            2   
701  grantmaking, giving, and social advocacy organ...   58458            3   
702  civic, social, professional, and similar organ...   95191            4   

     Ratio_in_Product     Sales_Sum  Sale Share  
0        16379.000000  2.693500e+04    0.608094  
1        10556.000000  2.693500e+04    0.391906  
2        16379.000000  1.637900e+04    1.000000  
3       215421.000000  2.154210e+05    1.000000  
4         1793.833333  1.793833e+03    1.000000  
..                ...           ...         ...  
698       6964.666667  1.554667e+06    0.004480  
699      27244.666667  1.554667e+06    0.017524  
700      50101.000000  1.554667e+06    0.032226  
701      19486.000000  1.554667e+06    0.012534  
702      23797.750000  1.554667e+06    0.015307  

[703 rows x 7 columns]

# 9. Merge Sale shares and Delta

In [23]:
df_reset = delta_products.reset_index()
delta_products = df_reset.rename(columns={'index': 'product'})
delta_products_saleshare = delta_products.merge(product_sales, how = 'inner', on = ['industry', 'product'])
delta_products_saleshare = delta_products_saleshare.drop(columns=['Sales_Sum', "Ratio_in_Product", "In#Products", "Sales", "industry"])
delta_products_saleshare = delta_products_saleshare.set_index(delta_products_saleshare.columns[0])
delta_products_saleshare

accessories and parts  \
product                                                                    
tools, hardware, and supplies                                   0.007275   
group housing                                                   0.000399   
amusement parks, campgrounds, and related recre...              0.000399   
hotels and motels                                               0.000399   
housing at schools                                              0.000399   
...                                                                  ...   
less: expenditures in the united states by nonr...              0.001175   
government employees' expenditures abroad                       0.003612   
private employees' expenditures abroad                          0.003612   
u.s. travel outside the united states                           0.003612   
u.s. student expenditures                                       0.003612   

                                                   air transportation  \
product                                                                 
tools, hardware, and supplies                                0.000458   
group housing                                                0.000019   
amusement parks, campgrounds, and related recre...           0.000019   
hotels and motels                                            0.000019   
housing at schools                                           0.000019   
...                                                               ...   
less: expenditures in the united states by nonr...           0.000352   
government employees' expenditures abroad                    0.000083   
private employees' expenditures abroad                       0.000083   
u.s. travel outside the united states                        0.000083   
u.s. student expenditures                                    0.000083   

                                                   alcohol in purchased meals  \
product                                                                         
tools, hardware, and supplies                                        0.003963   
group housing                                                        0.001152   
amusement parks, campgrounds, and related recre...                   0.001152   
hotels and motels                                                    0.001152   
housing at schools                                                   0.001152   
...                                                                       ...   
less: expenditures in the united states by nonr...                   0.002213   
government employees' expenditures abroad                            0.000903   
private employees' expenditures abroad                               0.000903   
u.s. travel outside the united states                                0.000903   
u.s. student expenditures                                            0.000903   

                                                   all other professional medical services  \
product                                                                                      
tools, hardware, and supplies                                                     0.000174   
group housing                                                                      0.00002   
amusement parks, campgrounds, and related recre...                                 0.00002   
hotels and motels                                                                  0.00002   
housing at schools                                                                 0.00002   
...                                                                                    ...   
less: expenditures in the united states by nonr...                                0.000039   
government employees' expenditures abroad                                         0.002489   
private employees' expenditures abroad                                            0.002489   
u.s. travel outside the 

# 10. weightTimesDeltaValue + 11.

In [24]:
# Convert from Wide to Long
delta_final = delta_products_saleshare.reset_index().melt(id_vars=[delta_products_saleshare.index.name, "Sale Share"],
                                var_name="Column Products", value_name="value")

# Just Renaming and Reordering
delta_final = delta_final.rename(columns={delta_products_saleshare.index.name: "Row Products"})
delta_final = delta_final[['Row Products', 'Column Products', 'value', 'Sale Share']]
# Calculating weightTimesDeltaValue
delta_final["weightTimesDeltaValue"] = delta_final["value"] * delta_final["Sale Share"]

# Sum weightTimesDeltaValue grouping by Row Products AND Column Products
delta_final = delta_final.groupby(['Row Products', 'Column Products']).sum()
delta_final
# Convert Back to Wide Format 
delta_final = delta_final.pivot_table(values='weightTimesDeltaValue', index='Row Products', columns='Column Products')

# Removes Index and Column Names cuz it looks better. Both Index and Columns are simply Product Categories now
delta_final.columns.name = None 
delta_final.index.name = None 
delta_final

accessories and parts  \
accessories and parts                                           0.137149   
air transportation                                              0.000044   
alcohol in purchased meals                                       0.00086   
all other professional medical services                         0.000841   
amusement parks, campgrounds, and related recre...              0.001156   
...                                                                  ...   
water transportation                                            0.002166   
window coverings                                                0.001774   
wine                                                            0.010569   
women's and girls' clothing                                     0.001929   
workers' compensation                                            0.00025   

                                                   air transportation  \
accessories and parts                                        0.000523   
air transportation                                            0.00004   
alcohol in purchased meals                                   0.000124   
all other professional medical services                       0.00008   
amusement parks, campgrounds, and related recre...           0.000184   
...                                                               ...   
water transportation                                         0.000501   
window coverings                                             0.000035   
wine                                                          0.00026   
women's and girls' clothing                                  0.000085   
workers' compensation                                        0.000004   

                                                   alcohol in purchased meals  \
accessories and parts                                                0.001871   
air transportation                                                    0.00116   
alcohol in purchased meals                                           0.001875   
all other professional medical services                              0.002635   
amusement parks, campgrounds, and related recre...                   0.001375   
...                                                                       ...   
water transportation                                                 0.001055   
window coverings                                                     0.000358   
wine                                                                 0.002293   
women's and girls' clothing                                          0.000584   
workers' compensation                                                0.000413   

                                                   all other professional medical services  \
accessories and parts                                                             0.000554   
air transportation                                                                 0.00003   
alcohol in purchased meals                                                        0.000078   
all other professional medical services                                           0.000362   
amusement parks, campgrounds, and related recre...                                0.000113   
...                                                                                    ...   
water transportation                                                              0.000093   
window coverings                                                                  0.000092   
wine                                                                              0.000113   
women's and girls' clothing                                                       0.000074   
workers' compensation                                                             0.000008   

                                                   amusement parks, campgrounds, and related recreational services  \
accessories and parts                    

# 12. Calculate Gamma

In [26]:
row_sums = delta_final.sum(axis=1)
gamma = pd.DataFrame(row_sums, columns=['Row_Sum'])
gamma.index = delta_final.index 
gamma

Row_Sum
accessories and parts                               0.502129
air transportation                                  0.062202
alcohol in purchased meals                          0.128128
all other professional medical services             0.088652
amusement parks, campgrounds, and related recre...  0.113412
...                                                      ...
water transportation                                0.156271
window coverings                                    0.119453
wine                                                0.481751
women's and girls' clothing                           0.0809
workers' compensation                               0.064778

[212 rows x 1 columns]

# 13. Calculate Omega

In [ ]:
delta_gamma = delta_final.merge(gamma, left_on=gamma.index, right_on=delta_final.index)
delta_gamma = delta_gamma.set_index(delta_gamma.columns[0])
row_sums = delta_gamma.iloc[:, -1]
row_sums[row_sums == 0] = np.nan
omega = delta_gamma.iloc[:, :-1].div(row_sums, axis=0)
omega.columns.name = None 
omega.index.name = None 
omega

accessories and parts  \
accessories and parts                                           0.273136   
air transportation                                              0.000709   
alcohol in purchased meals                                      0.006709   
all other professional medical services                         0.009486   
amusement parks, campgrounds, and related recre...               0.01019   
...                                                                  ...   
water transportation                                             0.01386   
window coverings                                                0.014853   
wine                                                            0.021938   
women's and girls' clothing                                     0.023843   
workers' compensation                                           0.003863   

                                                   air transportation  \
accessories and parts                                        0.001041   
air transportation                                           0.000638   
alcohol in purchased meals                                   0.000969   
all other professional medical services                      0.000905   
amusement parks, campgrounds, and related recre...            0.00162   
...                                                               ...   
water transportation                                         0.003203   
window coverings                                             0.000297   
wine                                                         0.000539   
women's and girls' clothing                                   0.00105   
workers' compensation                                        0.000064   

                                                   alcohol in purchased meals  \
accessories and parts                                                0.003725   
air transportation                                                   0.018648   
alcohol in purchased meals                                           0.014636   
all other professional medical services                              0.029727   
amusement parks, campgrounds, and related recre...                   0.012126   
...                                                                       ...   
water transportation                                                 0.006752   
window coverings                                                     0.002999   
wine                                                                 0.004759   
women's and girls' clothing                                          0.007215   
workers' compensation                                                0.006368   

                                                   all other professional medical services  \
accessories and parts                                                             0.001104   
air transportation                                                                0.000489   
alcohol in purchased meals                                                        0.000611   
all other professional medical services                                           0.004087   
amusement parks, campgrounds, and related recre...                                0.000994   
...                                                                                    ...   
water transportation                                                              0.000593   
window coverings                                                                   0.00077   
wine                                                                              0.000234   
women's and girls' clothing                                                        0.00092   
workers' compensation                                                             0.000124   

                                                   amusement parks, campgrounds, and related recreational services  \
accessories and parts                    

# Start of Doing our Supply/demand contribution graph properly (Which influenceer has hte most influence?)

In [ ]:
shaprio_proucts = pd.read_excel(os.path.join(Shapiro_data, 'shaprio_products.xlsx'))
shaprio_proucts = shaprio_proucts["Products"].to_frame()
shaprio_proucts['Products'] = shaprio_proucts['Products'].apply(lambda x: re.sub(r'\([^\)]*\d[^\)]*\)', '', x))
shaprio_proucts['Products'] = shaprio_proucts['Products'].str.rstrip()
shaprio_proucts['Products'] = shaprio_proucts['Products'].str.lower()

# gamma_shaprio = gamma[gamma["Unnamed: 0"].isin(shaprio_proucts['Products'])]
# gamma_shaprio.reset_index(drop=True, inplace=True)
# gamma_shaprio

Products
0                                            new autos
1                                     new light trucks
2                                           used autos
3                                    used light trucks
4                                                tires
..                                                 ...
125                     repair of household appliances
126                           other household services
127                   foreign travel by u.s. residents
128  less: expenditures in the united states by non...
129  final consumption expenditures of nonprofit in...

[130 rows x 1 columns]